# 1. Importo librerias

In [1]:
from binance.client import Client
from datetime import datetime
from backtesting import Backtest, Strategy
from backtesting.lib import plot_heatmaps

import multiprocessing
import pandas as pd


/Users/nelsonrios/opt/anaconda3/lib/python3.8/site-packages/backtesting/_plotting.py:45: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

# 2. Configuro ambiente y traigo datos historicos

In [2]:
## necesario por cuestiones de optimizacion de performance de la simulacion
multiprocessing.set_start_method('fork', force=True)

In [32]:
#TODO: mover a variables de entorno
api_key = ''
secret_key = ''

client = Client(api_key, secret_key)


bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '30 days ago')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '31 jul, 2021', '3 ago, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '29 jul, 2021', '31 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '27 jul, 2021', '29 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '25 jul, 2021', '27 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '23 jul, 2021', '25 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '21 jul, 2021', '23 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '19 jul, 2021', '21 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '17 jul, 2021', '19 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '15 jul, 2021', '17 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '13 jul, 2021', '15 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '11 jul, 2021', '13 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '7 jul, 2021', '9 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '5 jul, 2021', '7 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '3 jul, 2021', '5 jul, 2021')
# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '1 jul, 2021', '3 jul, 2021')


def cast_string_to_float(data):
    if type(data) == str:
        casted_data = float(data)
    else:
        casted_data = datetime.fromtimestamp(data/1000.0)
    return casted_data

# delete unwanted data - just keep date, open, high, low, close
formated_bars = []
for line in bars:
    del line[6:]
    # cast string numbers to integer
    formated_bars.append(list(map(cast_string_to_float, line)))

#  store data in a dataframe
btc_df = pd.DataFrame(formated_bars, columns=['Date', 'Open', 'High', 'Low', 'Close', 'Volume'])
btc_df.set_index('Date', inplace=True)
# Converting the index as date
btc_df.index = pd.to_datetime(btc_df.index)
btc_df

Open      High       Low     Close      Volume
Date                                                                   
2021-07-07 18:35:00  34286.87  34287.86  34196.86  34232.97   57.065316
2021-07-07 18:36:00  34232.98  34244.85  34220.01  34227.44   19.912194
2021-07-07 18:37:00  34227.89  34227.89  34207.12  34211.57   23.298738
2021-07-07 18:38:00  34211.57  34215.15  34122.01  34134.19   60.411503
2021-07-07 18:39:00  34134.20  34262.85  34112.50  34210.39  116.377553
...                       ...       ...       ...       ...         ...
2021-08-06 21:31:00  42782.93  42794.00  42714.47  42721.76   80.242070
2021-08-06 21:32:00  42723.48  42839.96  42721.01  42824.28   63.425440
2021-08-06 21:33:00  42825.04  42847.00  42825.04  42843.40   23.396698
2021-08-06 21:34:00  42843.41  42845.59  42804.05  42824.16   21.676535
2021-08-06 21:35:00  42824.16  42830.00  42824.16  42828.21   14.248887

[43381 rows x 5 columns]

# 3. Armo una estrategia de reversion con AROON


## 3.1 Estrategia

In [43]:

from talib import AROON, SMA
import pandas as pd

class AroonPullback(Strategy):

    AROON_FAST_LENGTH = 240
    AROON_SLOW_LENGTH = 1440

    def init(self):
        self.aroondown_fast, self.aroonup_fast = self.I(AROON, self.data.High, self.data.Low, timeperiod = self.AROON_FAST_LENGTH)
        self.aroondown_slow, self.aroonup_slow = self.I(AROON, self.data.High, self.data.Low, timeperiod = self.AROON_SLOW_LENGTH)
        self.ma = self.I(SMA, self.data.Close, 200)
        self.my_stop_loss = self.data.High

    def next(self):
        if (not self.position):
            if ((self.aroonup_fast == 100) and
                (self.aroonup_slow != 100)):
                self.sell(sl=(self.my_stop_loss), tp=(self.data.Close * .995))
            if (self.aroonup_slow == 100):
                self.my_stop_loss = self.data.High
        # else:
        #     if (self.position.is_short and self.data.Low <= self.mean_price or
        #         self.diff_vol > 2.4):
        #         self.position.close()

## 3.2 Resultados

In [44]:
bt = Backtest(btc_df, AroonPullback, cash=1000000, commission=.0004, exclusive_orders=True)
stats = bt.run()
stats

Start                     2021-07-07 18:35:00
End                       2021-08-06 21:35:00
Duration                     30 days 03:00:00
Exposure Time [%]                   76.171596
Equity Final [$]                643596.544378
Equity Peak [$]                1126317.044378
Return [%]                         -35.640346
Buy & Hold Return [%]               25.108076
Return (Ann.) [%]                  -99.442069
Volatility (Ann.) [%]                0.912307
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -42.858314
Avg. Drawdown [%]                   -0.597614
Max. Drawdown Duration       16 days 21:31:00
Avg. Drawdown Duration        0 days 04:35:00
# Trades                                   27
Win Rate [%]                        96.296296
Best Trade [%]                       0.465148
Worst Trade [%]                    -43.462011
Avg. Trade [%]                    

In [45]:
bt.plot()



/Users/nelsonrios/opt/anaconda3/lib/python3.8/site-packages/backtesting/_plotting.py:104: UserWarning: Data contains too many candlesticks to plot; downsampling to '5T'. See `Backtest.plot(resample=...)`
  warnings.warn(f"Data contains too many candlesticks to plot; downsampling to {freq!r}. "


In [13]:
## Reviso Volatilidad de trades

In [288]:
stats._trades.sort_values('ReturnPct').head(20)

Size  EntryBar  ExitBar   EntryPrice  ExitPrice           PnL  \
285    386      9272     9297  2556.172060    2304.07 -97311.395160   
305    383      9987    10018  2408.753116    2231.96 -67711.763428   
470    451     15245    15284  1890.305820    1769.10 -54663.824820   
464    434     15026    15068  2045.547892    1922.10 -53576.385128   
1799  -264     65990    66033  1835.555484    1931.99 -25458.712224   
374    327     12253    12271  2681.031984    2541.60 -45594.258768   
284    371      9192     9215  2799.859496    2663.79 -50481.783016   
328    309     10921    10942  2829.181220    2697.40 -40720.396980   
499   -380     16115    16154  2149.799736    2231.36 -30992.900320   
1133   215     37469    37499  2585.413752    2491.16 -20264.556680   
409   -371     13471    13500  2365.063596    2450.68 -31763.685884   
380    356     12557    12585  2423.969200    2342.00 -29181.035200   
1516   241     56426    56445  2084.513472    2015.70 -16584.046752   
307   -345     10200    10230  2498.320272    2571.86 -25371.206160   
690    294     22007    22033  2549.969580    2476.13 -21708.836520   
1480   239     55194    55234  2166.696332    2104.36 -14898.383348   
287   -371      9419     9443  2574.889632    2648.28 -27227.826528   
1151   217     38152    38180  2462.204488    2393.64 -14878.493896   
290   -341      9514     9530  2746.231068    2821.10 -25530.305812   
294    349      9603     9621  2720.947944    2647.31 -25699.642456   

      ReturnPct           EntryTime            ExitTime        Duration  
285   -0.098625 2021-05-19 09:34:00 2021-05-19 09:59:00 0 days 00:25:00  
305   -0.073396 2021-05-19 21:29:00 2021-05-19 22:00:00 0 days 00:31:00  
470   -0.064120 2021-05-23 13:07:00 2021-05-23 13:46:00 0 days 00:39:00  
464   -0.060350 2021-05-23 09:28:00 2021-05-23 10:10:00 0 days 00:42:00  
1799  -0.052537 2021-06-27 18:52:00 2021-06-27 19:35:00 0 days 00:43:00  
374   -0.052007 2021-05-21 11:15:00 2021-05-21 11:33:00 0 days 00:18:00  
284   -0.048599 2021-05-19 08:14:00 2021-05-19 08:37:00 0 days 00:23:00  
328   -0.046579 2021-05-20 13:03:00 2021-05-20 13:24:00 0 days 00:21:00  
499   -0.037939 2021-05-24 03:37:00 2021-05-24 04:16:00 0 days 00:39:00  
1133  -0.036456 2021-06-07 23:31:00 2021-06-08 00:01:00 0 days 00:30:00  
409   -0.036200 2021-05-22 07:33:00 2021-05-22 08:02:00 0 days 00:29:00  
380   -0.033816 2021-05-21 16:19:00 2021-05-21 16:47:00 0 days 00:28:00  
1516  -0.033012 2021-06-21 03:28:00 2021-06-21 03:47:00 0 days 00:19:00  
307   -0.029436 2021-05-20 01:02:00 2021-05-20 01:32:00 0 days 00:30:00  
690   -0.028957 2021-05-28 05:49:00 2021-05-28 06:15:00 0 days 00:26:00  
1480  -0.028770 2021-06-20 06:56:00 2021-06-20 07:36:00 0 days 00:40:00  
287   -0.028502 2021-05-19 12:01:00 2021-05-19 12:25:00 0 days 00:24:00  
1151  -0.027847 2021-06-08 10:54:00 2021-06-08 11:22:00 0 days 00:28:00  
290   -0.027262 2021-05-19 13:36:00 2021-05-19 13:52:00 0 days 00:16:00  
294   -0.027063 2021-05-19 15:05:00 2021-05-19 15:23:00 0 days 00:18:00

In [278]:
trades_btc = stats._trades
trades_btc['type'] = 0

trades_btc

Size  EntryBar  ExitBar    EntryPrice  ExitPrice           PnL  \
0     -19      3069     3075  50433.588492   49944.47   9293.251348   
1     -19      3158     3175  50569.744008   50504.89   1232.226152   
2     -20      3274     3290  50441.805204   50800.00  -7163.895920   
3     -19      3650     3655  50171.173500   49887.73   5385.426500   
4     -20      3725     3737  49611.937284   49584.19    554.945680   
..    ...       ...      ...           ...        ...           ...   
179    38     71437    71442  35415.910700   35722.66  11656.473400   
180   -41     74497    74508  33409.880700   33439.00  -1193.891300   
181   -40     81526    81533  34143.097296   33992.57   6021.091840   
182    39     82712    82717  34648.593896   34792.07   5595.568056   
183    39     82997    83010  34819.682304   34801.48   -709.889856   

     ReturnPct           EntryTime            ExitTime        Duration  type  
0     0.009698 2021-05-12 21:35:00 2021-05-12 21:41:00 0 days 00:06:00     0  
1     0.001282 2021-05-12 23:04:00 2021-05-12 23:21:00 0 days 00:17:00     0  
2    -0.007101 2021-05-13 01:00:00 2021-05-13 01:16:00 0 days 00:16:00     0  
3     0.005650 2021-05-13 07:16:00 2021-05-13 07:21:00 0 days 00:05:00     0  
4     0.000559 2021-05-13 08:31:00 2021-05-13 08:43:00 0 days 00:12:00     0  
..         ...                 ...                 ...             ...   ...  
179   0.008661 2021-06-29 09:03:00 2021-06-29 09:08:00 0 days 00:05:00     0  
180  -0.000872 2021-07-01 12:03:00 2021-07-01 12:14:00 0 days 00:11:00     0  
181   0.004409 2021-07-06 09:12:00 2021-07-06 09:19:00 0 days 00:07:00     0  
182   0.004141 2021-07-07 04:58:00 2021-07-07 05:03:00 0 days 00:05:00     0  
183  -0.000523 2021-07-07 09:43:00 2021-07-07 09:56:00 0 days 00:13:00     0  

[184 rows x 11 columns]

## 3.3 Optimizacion

### Optimizacion EMA


In [75]:
%%time
stats, heatmap = bt.optimize(BULL_BEAR_MARKET_EMA_THRESHOLD = range(185,901,5), maximize='Return [%]',return_heatmap=True)

CPU times: user 6.05 s, sys: 236 ms, total: 6.28 s
Wall time: 12min


In [79]:
stats

Start                     2021-05-10 17:00:00
End                       2021-07-09 20:01:00
Duration                     60 days 03:01:00
Exposure Time [%]                    2.314569
Equity Final [$]               1364527.308192
Equity Peak [$]                1364527.308192
Return [%]                          36.452731
Buy & Hold Return [%]              -38.790955
Return (Ann.) [%]                  542.215179
Volatility (Ann.) [%]              174.555218
Sharpe Ratio                         3.106267
Sortino Ratio                       82.872904
Calmar Ratio                       119.964073
Max. Drawdown [%]                   -4.519813
Avg. Drawdown [%]                   -0.526369
Max. Drawdown Duration        8 days 07:17:00
Avg. Drawdown Duration        0 days 11:36:00
# Trades                                  177
Win Rate [%]                        69.491525
Best Trade [%]                       1.772976
Worst Trade [%]                     -2.856759
Avg. Trade [%]                    

In [80]:
stats._strategy


<Strategy AroonPullback(BULL_BEAR_MARKET_EMA_THRESHOLD=835)>

In [81]:
heatmap.sort_values().tail(10)

BULL_BEAR_MARKET_EMA_THRESHOLD
775                               35.917866
760                               36.037637
755                               36.037637
750                               36.037637
765                               36.098765
830                               36.367655
845                               36.452731
850                               36.452731
835                               36.452731
840                               36.452731
Name: Return [%], dtype: float64

### Optimizacion volumen

In [230]:
%%time
stats, heatmap = bt.optimize(VOLUME_THRESHOLD = range(10,31, 5), VOLUME_LENGTH = range(5,20,5), return_heatmap=True)

CPU times: user 8.21 s, sys: 266 ms, total: 8.48 s
Wall time: 1min 38s


In [231]:
stats

Start                     2021-05-10 18:26:00
End                       2021-07-09 21:27:00
Duration                     60 days 03:01:00
Exposure Time [%]                    2.544409
Equity Final [$]               1268568.395116
Equity Peak [$]                1269200.011508
Return [%]                           26.85684
Buy & Hold Return [%]              -38.561976
Return (Ann.) [%]                   315.13529
Volatility (Ann.) [%]               102.58427
Sharpe Ratio                         3.071965
Sortino Ratio                       28.889541
Calmar Ratio                        47.171073
Max. Drawdown [%]                   -6.680689
Avg. Drawdown [%]                   -0.515733
Max. Drawdown Duration       11 days 21:58:00
Avg. Drawdown Duration        0 days 14:20:00
# Trades                                  198
Win Rate [%]                         70.20202
Best Trade [%]                       1.772976
Worst Trade [%]                     -3.894395
Avg. Trade [%]                    

In [233]:
stats._strategy



<Strategy AroonPullback(VOLUME_THRESHOLD=20,VOLUME_LENGTH=15)>

In [555]:
heatmap.sort_values().tail(10)

VOLUME_THRESHOLD  VOLUME_LENGTH
30                20              NaN
Name: SQN, dtype: float64

In [232]:
plot_heatmaps(heatmap, agg='mean')

Column(id='28492', ...)

### Optimizacion SMA reversion


In [319]:
%%time
stats, heatmap = bt.optimize(SMA_LENGTH = range(7,20), return_heatmap=True)

CPU times: user 7.19 s, sys: 237 ms, total: 7.42 s
Wall time: 1min 12s


In [320]:
stats

Start                     2021-05-12 22:40:00
End                       2021-07-12 01:41:00
Duration                     60 days 03:01:00
Exposure Time [%]                   12.971518
Equity Final [$]                2276305.75268
Equity Peak [$]                 2283868.69268
Return [%]                         127.630575
Buy & Hold Return [%]                -31.2622
Return (Ann.) [%]                12578.009971
Volatility (Ann.) [%]             7815.966402
Sharpe Ratio                         1.609271
Sortino Ratio                      1025.57876
Calmar Ratio                       818.380336
Max. Drawdown [%]                  -15.369394
Avg. Drawdown [%]                   -0.716582
Max. Drawdown Duration        5 days 14:42:00
Avg. Drawdown Duration        0 days 03:49:00
# Trades                                  978
Win Rate [%]                        66.257669
Best Trade [%]                       3.666382
Worst Trade [%]                     -7.239913
Avg. Trade [%]                    

In [321]:
stats._strategy

<Strategy AroonPullback(SMA_LENGTH=15)>

In [322]:
heatmap.sort_values()

SMA_LENGTH
7             1.643722
8             2.059221
9             2.182061
10            2.589117
18            2.860532
11            2.963703
19            3.052627
12            3.374022
14            3.419381
13            3.512165
17            3.594334
16            3.813953
15            3.976751
Name: SQN, dtype: float64

### Optimizacion NATR de activacion

In [310]:
%%time
stats, heatmap = bt.optimize(NATR_THRESHOLD_MR = range(25,50), return_heatmap=True)

CPU times: user 7.58 s, sys: 244 ms, total: 7.82 s
Wall time: 1min 59s


In [311]:
stats

Start                     2021-05-12 22:40:00
End                       2021-07-12 01:41:00
Duration                     60 days 03:01:00
Exposure Time [%]                   12.971518
Equity Final [$]                2276305.75268
Equity Peak [$]                 2283868.69268
Return [%]                         127.630575
Buy & Hold Return [%]                -31.2622
Return (Ann.) [%]                12578.009971
Volatility (Ann.) [%]             7815.966402
Sharpe Ratio                         1.609271
Sortino Ratio                      1025.57876
Calmar Ratio                       818.380336
Max. Drawdown [%]                  -15.369394
Avg. Drawdown [%]                   -0.716582
Max. Drawdown Duration        5 days 14:42:00
Avg. Drawdown Duration        0 days 03:49:00
# Trades                                  978
Win Rate [%]                        66.257669
Best Trade [%]                       3.666382
Worst Trade [%]                     -7.239913
Avg. Trade [%]                    

In [314]:
stats._strategy

<Strategy AroonPullback(NATR_THRESHOLD_MR=36)>

In [313]:
heatmap.sort_values().tail(10)

NATR_THRESHOLD_MR
40                   3.591003
32                   3.594712
41                   3.624573
29                   3.648866
30                   3.701418
35                   3.774752
38                   3.821365
39                   3.835548
37                   3.882370
36                   3.976751
Name: SQN, dtype: float64

### Optimizacion de ventana de Aroon

In [50]:
%%time
stats, heatmap = bt.optimize(AROON_LENGTH = range(5,60,5), return_heatmap=True)

CPU times: user 13.1 s, sys: 476 ms, total: 13.6 s
Wall time: 2min 10s


In [51]:
stats

Start                     2021-04-10 15:40:00
End                       2021-07-09 18:43:00
Duration                     90 days 03:03:00
Exposure Time [%]                    0.637804
Equity Final [$]               1187978.711492
Equity Peak [$]                1188997.886992
Return [%]                          18.797871
Buy & Hold Return [%]              -43.328821
Return (Ann.) [%]                   99.552285
Volatility (Ann.) [%]               21.257616
Sharpe Ratio                         4.683135
Sortino Ratio                       36.550578
Calmar Ratio                        43.871848
Max. Drawdown [%]                   -2.269161
Avg. Drawdown [%]                   -0.466214
Max. Drawdown Duration       13 days 18:16:00
Avg. Drawdown Duration        0 days 20:17:00
# Trades                                   83
Win Rate [%]                        68.674699
Best Trade [%]                       1.064826
Worst Trade [%]                     -0.916845
Avg. Trade [%]                    

In [54]:
stats._strategy

<Strategy AroonPullback(AROON_LENGTH=30)>

In [55]:
heatmap.sort_values()

AROON_LENGTH
5               1.119235
45              2.676716
40              2.688224
55              2.689207
50              2.840747
15              2.900761
25              3.042497
10              3.269772
20              3.406104
35              3.545709
30              4.343172
Name: SQN, dtype: float64

### Optimizo valores de volatilidad

In [331]:
%%time
stats, heatmap = bt.optimize(VOLATILITY_THRESHOLD = range(80, 120), return_heatmap=True)

CPU times: user 7.2 s, sys: 230 ms, total: 7.43 s
Wall time: 3min 2s


In [332]:
stats

Start                     2021-05-12 22:40:00
End                       2021-07-12 01:41:00
Duration                     60 days 03:01:00
Exposure Time [%]                   12.117992
Equity Final [$]               2314394.640752
Equity Peak [$]                2322072.170752
Return [%]                         131.439464
Buy & Hold Return [%]                -31.2622
Return (Ann.) [%]                13879.071626
Volatility (Ann.) [%]             8482.206998
Sharpe Ratio                         1.636257
Sortino Ratio                     1455.175033
Calmar Ratio                       903.518946
Max. Drawdown [%]                   -15.36113
Avg. Drawdown [%]                   -0.709186
Max. Drawdown Duration        6 days 08:04:00
Avg. Drawdown Duration        0 days 04:00:00
# Trades                                  921
Win Rate [%]                        67.100977
Best Trade [%]                       3.666382
Worst Trade [%]                     -7.239913
Avg. Trade [%]                    

In [333]:
stats._strategy

<Strategy AroonPullback(VOLATILITY_THRESHOLD=115)>

In [334]:
heatmap.sort_values()

VOLATILITY_THRESHOLD
80                      3.814714
81                      3.814714
82                      3.827571
83                      3.839926
85                      3.840376
86                      3.840376
84                      3.845240
87                      3.863034
88                      3.863034
108                     3.876590
90                      3.893656
89                      3.906102
91                      3.919325
106                     3.942014
93                      3.947000
94                      3.947000
107                     3.958605
92                      3.964879
100                     3.976751
102                     3.977868
101                     3.981828
109                     3.993687
104                     4.004584
105                     4.008358
98                      4.010713
112                     4.013609
103                     4.020895
113                     4.020895
99                      4.022258
111                   

## 4. Pruebo con altcoins

In [20]:
from talib import AROON, SMA, NATR, AROONOSC
import pandas as pd

class EthAroonPullback(Strategy):

    AROON_LENGTH = 30
    VOLUME_LENGTH = 10
    VOLUME_THRESHOLD = 15
    SMA_LENGTH = 15
    NATR_THRESHOLD_MR = 36
    VOLATILITY_LENGTH = 60
    VOLATILITY_THRESHOLD = 0

    def VOLUME_AVG(self, volume):
       return pd.Series(volume).rolling(self.VOLUME_LENGTH).mean()

    def EMA_AVG(self, data):
        return pd.Series(data).ewm(span=self.BULL_BEAR_MARKET_EMA_THRESHOLD).mean()

    def STD_DEV(self, data):
        pct_changes = pd.Series(data).pct_change() * 100
        return pct_changes.rolling(self.VOLATILITY_LENGTH).std() 

    def init(self):
        self.aroondown, self.aroonup = self.I(AROON, self.data.High, self.data.Low, timeperiod = self.AROON_LENGTH)
        self.volume_avg = self.I(self.VOLUME_AVG, self.data.Volume)
        self.mean_price = self.I(SMA, self.data.Close, timeperiod=self.SMA_LENGTH)
        self.natr = self.I(NATR, self.data.High, self.data.Low, self.data.Close, timeperiod = 2)
        self.std_dev = self.I(self.STD_DEV, self.data.Close)

    def next(self):
        if (not self.position and self.natr > (self.NATR_THRESHOLD_MR/100)):
            if (self.aroonup == 100 and self.data.Volume > (self.VOLUME_THRESHOLD / 10 * self.volume_avg)):
                if (self.is_market_volatility_high()):
                    self.sell()
            elif(self.aroondown == 100 and self.data.Volume > (self.VOLUME_THRESHOLD / 10 * self.volume_avg)):
                if (self.is_market_volatility_high()):
                    self.buy()
        else:
            if (self.position.is_long and self.data.Close >= self.mean_price):
                self.position.close()
            elif (self.position.is_short and self.data.Close <= self.mean_price):
                self.position.close()

    def is_market_volatility_high(self):
        return self.std_dev > (self.VOLATILITY_THRESHOLD / 1000)

    def isMarketDowntrending(self):
        return (self.data.Close < self.ema)

    def isMarketUptrending(self):
        return (self.data.Close > self.ema)
                

In [18]:
#TODO: mover a variables de entorno
api_key = ''
secret_key = ''

client = Client(api_key, secret_key)


# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '14 jun, 2021', '17 jun, 2021')
bars = client.get_historical_klines('ETHUSDT', Client.KLINE_INTERVAL_1MINUTE, '60 days ago')


def cast_string_to_float(data):
    if type(data) == str:
        casted_data = float(data)
    else:
        casted_data = datetime.fromtimestamp(data/1000.0)
    return casted_data

# delete unwanted data - just keep date, open, high, low, close
formated_bars = []
for line in bars:
    del line[6:]
    # cast string numbers to integer
    formated_bars.append(list(map(cast_string_to_float, line)))

#  store data in a dataframe
eth_df = pd.DataFrame(formated_bars, columns=['Date', 'Open', 'High', 'Low', 'Close', 'Volume'])
eth_df.set_index('Date', inplace=True)
# Converting the index as date
eth_df.index = pd.to_datetime(eth_df.index)
eth_df

Open     High      Low    Close      Volume
Date                                                               
2021-05-14 10:19:00  3976.07  3976.44  3970.00  3971.16   794.53209
2021-05-14 10:20:00  3971.24  3976.84  3969.41  3969.41   525.37422
2021-05-14 10:21:00  3969.42  3969.99  3960.00  3962.99   808.97590
2021-05-14 10:22:00  3962.98  3965.66  3950.29  3955.97  1932.38727
2021-05-14 10:23:00  3955.97  3964.60  3952.89  3953.50   940.41542
...                      ...      ...      ...      ...         ...
2021-07-13 13:16:00  1991.38  1993.35  1991.12  1993.14   366.77835
2021-07-13 13:17:00  1993.00  1993.00  1990.00  1990.80   209.99161
2021-07-13 13:18:00  1990.80  1994.18  1990.79  1993.50   387.25387
2021-07-13 13:19:00  1993.65  1993.82  1991.21  1991.79   264.69901
2021-07-13 13:20:00  1991.79  1996.23  1991.70  1996.15   112.46991

[86582 rows x 5 columns]

In [21]:
bt_2 = Backtest(eth_df, EthAroonPullback, cash=1000000, commission=.0004, exclusive_orders=True)
stats = bt_2.run()
stats

Start                     2021-05-14 10:19:00
End                       2021-07-13 13:20:00
Duration                     60 days 03:01:00
Exposure Time [%]                   32.160264
Equity Final [$]                348722.343612
Equity Peak [$]                1053523.402608
Return [%]                         -65.127766
Buy & Hold Return [%]              -49.733831
Return (Ann.) [%]                  -99.838929
Volatility (Ann.) [%]                0.110919
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -69.522636
Avg. Drawdown [%]                   -3.842503
Max. Drawdown Duration       58 days 16:14:00
Avg. Drawdown Duration        2 days 20:30:00
# Trades                                 2310
Win Rate [%]                        61.385281
Best Trade [%]                       7.354071
Worst Trade [%]                     -9.862484
Avg. Trade [%]                    

In [22]:
bt_2.plot()

/Users/nelsonrios/opt/anaconda3/lib/python3.8/site-packages/backtesting/_plotting.py:104: UserWarning: Data contains too many candlesticks to plot; downsampling to '10T'. See `Backtest.plot(resample=...)`
  warnings.warn(f"Data contains too many candlesticks to plot; downsampling to {freq!r}. "


In [38]:
stats, heatmap = bt_2.optimize(NATR_THRESHOLD_MR = range(20, 50), return_heatmap=True)

In [39]:
stats

Start                     2021-05-14 10:19:00
End                       2021-07-13 13:20:00
Duration                     60 days 03:01:00
Exposure Time [%]                   14.151902
Equity Final [$]                748268.456904
Equity Peak [$]                1045152.891512
Return [%]                         -25.173154
Buy & Hold Return [%]              -49.733831
Return (Ann.) [%]                  -84.528402
Volatility (Ann.) [%]                9.128976
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -35.984298
Avg. Drawdown [%]                   -3.088489
Max. Drawdown Duration       58 days 20:20:00
Avg. Drawdown Duration        4 days 06:29:00
# Trades                                  989
Win Rate [%]                        60.465116
Best Trade [%]                       7.354071
Worst Trade [%]                     -9.862484
Avg. Trade [%]                    

In [40]:
heatmap

NATR_THRESHOLD_MR
20                  -2.371269
21                  -2.341796
22                  -2.257634
23                  -2.202106
24                  -2.023692
25                  -1.976864
26                  -1.819694
27                  -1.910454
28                  -1.755084
29                  -1.710107
30                  -1.580074
31                  -1.565617
32                  -1.417248
33                  -1.388343
34                  -1.346290
35                  -1.302004
36                  -1.173955
37                  -1.242961
38                  -1.160756
39                  -1.098535
40                  -1.083577
41                  -0.963712
42                  -0.966966
43                  -1.058601
44                  -0.994140
45                  -0.983819
46                  -1.140896
47                  -0.968218
48                  -1.079793
49                  -1.306472
Name: SQN, dtype: float64

In [280]:
trades_eth = stats._trades
trades_eth['type'] = 1
trades_eth

Size  EntryBar  ExitBar   EntryPrice  ExitPrice          PnL  ReturnPct  \
0    -240      1682     1695  4160.115288    4170.82 -2569.130880  -0.002573   
1    -242      1863     1872  4104.837408    4075.45  7111.752736   0.007159   
2    -252      2189     2193  3978.727872    3942.26  9189.903744   0.009166   
3    -257      2341     2352  3939.243672    3952.69 -3455.706296  -0.003413   
4    -270      2792     2798  3733.945824    3713.50  5520.372480   0.005476   
..    ...       ...      ...          ...        ...          ...        ...   
248   617     73801    73813  2113.875212    2109.22 -2872.265804  -0.002202   
249  -573     78790    78808  2269.391880    2283.27 -7952.162760  -0.006115   
250  -585     79499    79511  2211.125196    2218.65 -4402.010340  -0.003403   
251   554     80403    80411  2324.929600    2335.00  5579.001600   0.004331   
252   559     81399    81412  2316.436204    2315.18  -702.218036  -0.000542   

              EntryTime            ExitTime        Duration  type  
0   2021-05-12 14:01:00 2021-05-12 14:14:00 0 days 00:13:00     1  
1   2021-05-12 17:02:00 2021-05-12 17:11:00 0 days 00:09:00     1  
2   2021-05-12 22:28:00 2021-05-12 22:32:00 0 days 00:04:00     1  
3   2021-05-13 01:00:00 2021-05-13 01:11:00 0 days 00:11:00     1  
4   2021-05-13 08:31:00 2021-05-13 08:37:00 0 days 00:06:00     1  
..                  ...                 ...             ...   ...  
248 2021-07-01 16:00:00 2021-07-01 16:12:00 0 days 00:12:00     1  
249 2021-07-05 03:09:00 2021-07-05 03:27:00 0 days 00:18:00     1  
250 2021-07-05 14:58:00 2021-07-05 15:10:00 0 days 00:12:00     1  
251 2021-07-06 06:02:00 2021-07-06 06:10:00 0 days 00:08:00     1  
252 2021-07-06 22:38:00 2021-07-06 22:51:00 0 days 00:13:00     1  

[253 rows x 11 columns]

In [181]:
# ---------------- ETHUSDT --------------------
# Return [%]                          29.508357
# Buy & Hold Return [%]              -46.615276
# Return (Ann.) [%]                   369.83549
# Volatility (Ann.) [%]              134.582455
# Sharpe Ratio                         2.748022
# Sortino Ratio                       28.181807
# Calmar Ratio                        62.062087
# Max. Drawdown [%]                   -5.959121
# Avg. Drawdown [%]                   -0.847798
# Max. Drawdown Duration       23 days 20:36:00
# Avg. Drawdown Duration        0 days 14:42:00
# # Trades                                  253
# Win Rate [%]                        66.007905
# Best Trade [%]                       1.904153
# Worst Trade [%]                     -2.706334
# Avg. Trade [%]                       0.102406
# Max. Trade Duration           0 days 00:45:00
# Avg. Trade Duration           0 days 00:11:00
# Profit Factor                        1.485939
# Expectancy [%]                       0.104764
# SQN                                  2.337261

# ---------------- EOSUSDT --------------------
# Return [%]                          18.193087
# Buy & Hold Return [%]              -64.953173
# Return (Ann.) [%]                  224.812111
# Volatility (Ann.) [%]              112.250998
# Sharpe Ratio                         2.002763
# Sortino Ratio                       10.986823
# Calmar Ratio                        22.079498
# Max. Drawdown [%]                  -10.181939
# Avg. Drawdown [%]                   -1.282827
# Max. Drawdown Duration       23 days 02:22:00
# Avg. Drawdown Duration        0 days 23:07:00
# # Trades                                  387
# Win Rate [%]                        66.666667
# Best Trade [%]                       1.892271
# Worst Trade [%]                     -4.957256
# Avg. Trade [%]                       0.043201
# Max. Trade Duration           0 days 00:55:00
# Avg. Trade Duration           0 days 00:11:00
# Profit Factor                        1.179888
# Expectancy [%]                       0.046481
# SQN                                   1.04515

# ---------------- AXSUSDT --------------------
# Return [%]                          -7.783136
# Buy & Hold Return [%]              132.519478
# Return (Ann.) [%]                  -35.096962
# Volatility (Ann.) [%]               53.851152
# Sharpe Ratio                              0.0
# Sortino Ratio                             0.0
# Calmar Ratio                              0.0
# Max. Drawdown [%]                  -33.183431
# Avg. Drawdown [%]                   -1.992953
# Max. Drawdown Duration       52 days 03:37:00
# Avg. Drawdown Duration        2 days 07:17:00
# # Trades                                  533
# Win Rate [%]                        64.165103
# Best Trade [%]                       3.384944
# Worst Trade [%]                    -13.230799
# Avg. Trade [%]                      -0.015201
# Max. Trade Duration           0 days 00:56:00
# Avg. Trade Duration           0 days 00:11:00
# Profit Factor                        0.982331
# Expectancy [%]                      -0.006385
# SQN                                 -0.271708

# ---------------- XRPUSDT --------------------



In [217]:
bt_2.plot()

/Users/nelsonrios/opt/anaconda3/lib/python3.8/site-packages/backtesting/_plotting.py:104: UserWarning: Data contains too many candlesticks to plot; downsampling to '10T'. See `Backtest.plot(resample=...)`
  warnings.warn(f"Data contains too many candlesticks to plot; downsampling to {freq!r}. "


In [190]:
stats._trades.sort_values('ReturnPct').tail(20)

Size  EntryBar  ExitBar   EntryPrice  ExitPrice           PnL  ReturnPct  \
72   -386     15120    15122  2462.114760    2440.93   8177.317360   0.008604   
330  -551     65493    65499  1839.264000    1822.73   9110.234000   0.008989   
87   -486     17669    17676  1991.742984    1973.81   8715.430224   0.009004   
8    -248      2189     2193  3978.727872    3942.26   9044.032256   0.009166   
299  -497     59288    59291  1950.329556    1931.64   9288.709332   0.009583   
96    372     19078    19087  2540.655856    2565.16   9115.541568   0.009645   
79   -402     16207    16212  2319.161964    2295.41   9548.289528   0.010242   
143  -405     26105    26108  2334.465840    2310.40   9746.665200   0.010309   
101   363     19453    19459  2683.242868    2712.33  10558.628916   0.010840   
70   -382     14975    14984  2426.568984    2399.23  10443.491888   0.011267   
53   -371     11906    11912  2635.615332    2605.73  11087.458172   0.011339   
51   -320     11207    11212  3005.867172    2971.31  11058.295040   0.011497   
265  -368     52141    52142  2425.409448    2397.17  10392.116864   0.011643   
83   -450     17120    17127  2114.144004    2088.90  11359.801800   0.011941   
98    372     19244    19252  2589.845524    2622.87  12285.105072   0.012752   
59    330     13132    13138  2877.870688    2915.45  12401.172960   0.013058   
43   -297      9246     9250  3268.002276    3224.09  13041.945972   0.013437   
71   -383     15063    15066  2449.339872    2415.76  12861.090976   0.013710   
295  -468     58816    58820  2042.562648    2014.16  13292.439264   0.013905   
266  -370     52144    52152  2438.354268    2382.58  20636.479160   0.022874   

              EntryTime            ExitTime        Duration  
72  2021-05-21 21:59:00 2021-05-21 22:01:00 0 days 00:02:00  
330 2021-06-25 21:32:00 2021-06-25 21:38:00 0 days 00:06:00  
87  2021-05-23 16:28:00 2021-05-23 16:35:00 0 days 00:07:00  
8   2021-05-12 22:28:00 2021-05-12 22:32:00 0 days 00:04:00  
299 2021-06-21 14:07:00 2021-06-21 14:10:00 0 days 00:03:00  
96  2021-05-24 15:57:00 2021-05-24 16:06:00 0 days 00:09:00  
79  2021-05-22 16:06:00 2021-05-22 16:11:00 0 days 00:05:00  
143 2021-05-29 13:04:00 2021-05-29 13:07:00 0 days 00:03:00  
101 2021-05-24 22:12:00 2021-05-24 22:18:00 0 days 00:06:00  
70  2021-05-21 19:34:00 2021-05-21 19:43:00 0 days 00:09:00  
53  2021-05-19 16:25:00 2021-05-19 16:31:00 0 days 00:06:00  
51  2021-05-19 04:46:00 2021-05-19 04:51:00 0 days 00:05:00  
265 2021-06-16 15:00:00 2021-06-16 15:01:00 0 days 00:01:00  
83  2021-05-23 07:19:00 2021-05-23 07:26:00 0 days 00:07:00  
98  2021-05-24 18:43:00 2021-05-24 18:51:00 0 days 00:08:00  
59  2021-05-20 12:51:00 2021-05-20 12:57:00 0 days 00:06:00  
43  2021-05-17 20:05:00 2021-05-17 20:09:00 0 days 00:04:00  
71  2021-05-21 21:02:00 2021-05-21 21:05:00 0 days 00:03:00  
295 2021-06-21 06:15:00 2021-06-21 06:19:00 0 days 00:04:00  
266 2021-06-16 15:03:00 2021-06-16 15:11:00 0 days 00:08:00

## 5. Optimizo altcoins


### ETHUSDT


In [253]:
bt_2 = Backtest(eth_df, AroonPullback, cash=1000000, commission=.0004, exclusive_orders=True)
stats = bt_2.run()
stats

Start                     2021-05-11 09:59:00
End                       2021-07-10 13:00:00
Duration                     60 days 03:01:00
Exposure Time [%]                    4.983715
Equity Final [$]               1345736.006364
Equity Peak [$]                 1366693.65576
Return [%]                          34.573601
Buy & Hold Return [%]              -46.615276
Return (Ann.) [%]                  478.305864
Volatility (Ann.) [%]              191.513219
Sharpe Ratio                         2.497508
Sortino Ratio                       29.096883
Calmar Ratio                        48.163927
Max. Drawdown [%]                    -9.93079
Avg. Drawdown [%]                   -0.704388
Max. Drawdown Duration       28 days 00:28:00
Avg. Drawdown Duration        0 days 11:21:00
# Trades                                  380
Win Rate [%]                        65.789474
Best Trade [%]                       1.904153
Worst Trade [%]                     -2.706334
Avg. Trade [%]                    

### Bull Bear Threshold

In [202]:
%%time
stats, heatmap = bt_2.optimize(BULL_BEAR_MARKET_EMA_THRESHOLD = range(30,901,5), maximize='Return [%]',return_heatmap=True)

CPU times: user 9.12 s, sys: 302 ms, total: 9.42 s
Wall time: 14min 50s


In [203]:
stats

Start                     2021-05-11 09:59:00
End                       2021-07-10 13:00:00
Duration                     60 days 03:01:00
Exposure Time [%]                    3.163475
Equity Final [$]               1199573.537272
Equity Peak [$]                1203228.077264
Return [%]                          19.957354
Buy & Hold Return [%]              -46.615276
Return (Ann.) [%]                  190.655265
Volatility (Ann.) [%]               63.997778
Sharpe Ratio                         2.979092
Sortino Ratio                       16.123958
Calmar Ratio                        35.147038
Max. Drawdown [%]                   -5.424504
Avg. Drawdown [%]                   -0.733578
Max. Drawdown Duration       22 days 16:35:00
Avg. Drawdown Duration        0 days 16:14:00
# Trades                                  231
Win Rate [%]                        64.069264
Best Trade [%]                        1.39054
Worst Trade [%]                     -2.706334
Avg. Trade [%]                    

In [204]:
stats._strategy

<Strategy AroonPullback(BULL_BEAR_MARKET_EMA_THRESHOLD=300)>

In [207]:
heatmap.sort_values()

BULL_BEAR_MARKET_EMA_THRESHOLD
85                                -1.287782
30                                 0.424181
35                                 0.424181
80                                 0.844026
40                                 0.903006
                                    ...    
295                               18.945044
310                               19.083126
280                               19.169007
305                               19.261380
300                               19.957354
Name: Return [%], Length: 175, dtype: float64

In [205]:
stats._trades.sort_values('ReturnPct')

Size  EntryBar  ExitBar   EntryPrice  ExitPrice           PnL  ReturnPct  \
28    374     11826    11844  2720.947944    2647.31 -27540.591056  -0.027063   
13   -274      6428     6451  3698.330076    3790.00 -25117.559176  -0.024787   
103  -440     30269    30292  2581.886832    2629.92 -21134.593920  -0.018604   
139  -445     42992    43022  2520.581364    2561.92 -18395.693020  -0.016400   
32    375     12730    12755  2648.799096    2610.76 -14264.661000  -0.014361   
..    ...       ...      ...          ...        ...           ...        ...   
51   -493     17120    17127  2114.144004    2088.90  12445.293972   0.011941   
60    409     19244    19252  2589.845524    2622.87  13507.010684   0.012752   
34    342     13132    13138  2877.870688    2915.45  12852.124704   0.013058   
21   -301      9246     9250  3268.002276    3224.09  13217.595076   0.013437   
175  -559     58816    58820  2042.562648    2014.16  15877.080232   0.013905   

              EntryTime            ExitTime        Duration  
28  2021-05-19 15:05:00 2021-05-19 15:23:00 0 days 00:18:00  
13  2021-05-15 21:07:00 2021-05-15 21:30:00 0 days 00:23:00  
103 2021-06-01 10:28:00 2021-06-01 10:51:00 0 days 00:23:00  
139 2021-06-10 06:31:00 2021-06-10 07:01:00 0 days 00:30:00  
32  2021-05-20 06:09:00 2021-05-20 06:34:00 0 days 00:25:00  
..                  ...                 ...             ...  
51  2021-05-23 07:19:00 2021-05-23 07:26:00 0 days 00:07:00  
60  2021-05-24 18:43:00 2021-05-24 18:51:00 0 days 00:08:00  
34  2021-05-20 12:51:00 2021-05-20 12:57:00 0 days 00:06:00  
21  2021-05-17 20:05:00 2021-05-17 20:09:00 0 days 00:04:00  
175 2021-06-21 06:15:00 2021-06-21 06:19:00 0 days 00:04:00  

[231 rows x 10 columns]

### Volume

In [222]:
%%time
stats, heatmap = bt.optimize(VOLUME_THRESHOLD = range(10,51, 5), VOLUME_LENGTH = range(5,30,5),maximize='Return [%]', return_heatmap=True)

CPU times: user 8.54 s, sys: 310 ms, total: 8.85 s
Wall time: 4min 16s


In [223]:
stats

Start                     2021-05-10 18:26:00
End                       2021-07-09 21:27:00
Duration                     60 days 03:01:00
Exposure Time [%]                    3.810261
Equity Final [$]               1330508.270492
Equity Peak [$]                1336385.616648
Return [%]                          33.050827
Buy & Hold Return [%]              -38.561976
Return (Ann.) [%]                  452.169477
Volatility (Ann.) [%]              149.350666
Sharpe Ratio                         3.027569
Sortino Ratio                       39.961602
Calmar Ratio                        66.872482
Max. Drawdown [%]                   -6.761667
Avg. Drawdown [%]                   -0.683897
Max. Drawdown Duration       11 days 22:57:00
Avg. Drawdown Duration        0 days 12:19:00
# Trades                                  293
Win Rate [%]                        69.624573
Best Trade [%]                       3.103065
Worst Trade [%]                     -3.894395
Avg. Trade [%]                    

In [224]:
stats._strategy

<Strategy AroonPullback(VOLUME_THRESHOLD=15,VOLUME_LENGTH=10)>

In [227]:
plot_heatmaps(heatmap, agg='mean')

Column(id='27283', ...)

In [240]:
%%time
stats, heatmap = bt.optimize(NATR_THRESHOLD_MR = range(25,50), maximize='Return [%]', return_heatmap=True)

CPU times: user 8.16 s, sys: 258 ms, total: 8.42 s
Wall time: 2min 14s


In [241]:
stats

Start                     2021-05-10 18:26:00
End                       2021-07-09 21:27:00
Duration                     60 days 03:01:00
Exposure Time [%]                     2.27761
Equity Final [$]               1385201.169704
Equity Peak [$]                1386351.279704
Return [%]                          38.520117
Buy & Hold Return [%]              -38.561976
Return (Ann.) [%]                  602.679389
Volatility (Ann.) [%]              189.422904
Sharpe Ratio                         3.181661
Sortino Ratio                       57.839099
Calmar Ratio                       112.615199
Max. Drawdown [%]                    -5.35167
Avg. Drawdown [%]                   -0.593624
Max. Drawdown Duration       11 days 12:51:00
Avg. Drawdown Duration        0 days 10:54:00
# Trades                                  184
Win Rate [%]                        72.826087
Best Trade [%]                       3.103065
Worst Trade [%]                     -3.894395
Avg. Trade [%]                    

In [242]:
stats._strategy

<Strategy AroonPullback(NATR_THRESHOLD_MR=37)>

In [244]:
heatmap.sort_values()

NATR_THRESHOLD_MR
49                   20.732755
48                   20.904645
47                   22.832319
44                   25.338384
46                   26.246553
45                   26.277803
42                   26.992108
43                   27.416506
26                   29.347494
25                   29.555945
31                   29.635665
40                   30.704656
41                   30.867042
34                   32.013344
32                   32.443833
28                   32.503853
33                   32.686558
30                   33.050827
39                   33.669472
29                   33.955246
27                   34.045613
38                   35.659607
35                   38.174935
36                   38.446360
37                   38.520117
Name: Return [%], dtype: float64

### SMA to regress

In [256]:
%%time
stats, heatmap = bt_2.optimize(SMA_LENGTH = range(7,20), return_heatmap=True)

CPU times: user 9.92 s, sys: 331 ms, total: 10.2 s
Wall time: 1min 45s


In [257]:
stats

Start                     2021-05-11 09:59:00
End                       2021-07-10 13:00:00
Duration                     60 days 03:01:00
Exposure Time [%]                    4.983715
Equity Final [$]               1345736.006364
Equity Peak [$]                 1366693.65576
Return [%]                          34.573601
Buy & Hold Return [%]              -46.615276
Return (Ann.) [%]                  478.305864
Volatility (Ann.) [%]              191.513219
Sharpe Ratio                         2.497508
Sortino Ratio                       29.096883
Calmar Ratio                        48.163927
Max. Drawdown [%]                    -9.93079
Avg. Drawdown [%]                   -0.704388
Max. Drawdown Duration       28 days 00:28:00
Avg. Drawdown Duration        0 days 11:21:00
# Trades                                  380
Win Rate [%]                        65.789474
Best Trade [%]                       1.904153
Worst Trade [%]                     -2.706334
Avg. Trade [%]                    

In [258]:
stats._strategy

<Strategy AroonPullback(SMA_LENGTH=15)>

In [259]:
heatmap.sort_values()

SMA_LENGTH
7             0.271209
8             1.056024
10            1.537594
12            1.627269
13            1.739705
11            1.872095
9             1.888154
14            2.092869
18            2.118915
16            2.149423
17            2.163639
19            2.272422
15            2.439231
Name: SQN, dtype: float64

## Do trades overlap between btc and eth?

In [281]:
trades_btc

Size  EntryBar  ExitBar    EntryPrice  ExitPrice           PnL  \
0     -19      3069     3075  50433.588492   49944.47   9293.251348   
1     -19      3158     3175  50569.744008   50504.89   1232.226152   
2     -20      3274     3290  50441.805204   50800.00  -7163.895920   
3     -19      3650     3655  50171.173500   49887.73   5385.426500   
4     -20      3725     3737  49611.937284   49584.19    554.945680   
..    ...       ...      ...           ...        ...           ...   
179    38     71437    71442  35415.910700   35722.66  11656.473400   
180   -41     74497    74508  33409.880700   33439.00  -1193.891300   
181   -40     81526    81533  34143.097296   33992.57   6021.091840   
182    39     82712    82717  34648.593896   34792.07   5595.568056   
183    39     82997    83010  34819.682304   34801.48   -709.889856   

     ReturnPct           EntryTime            ExitTime        Duration  type  
0     0.009698 2021-05-12 21:35:00 2021-05-12 21:41:00 0 days 00:06:00     0  
1     0.001282 2021-05-12 23:04:00 2021-05-12 23:21:00 0 days 00:17:00     0  
2    -0.007101 2021-05-13 01:00:00 2021-05-13 01:16:00 0 days 00:16:00     0  
3     0.005650 2021-05-13 07:16:00 2021-05-13 07:21:00 0 days 00:05:00     0  
4     0.000559 2021-05-13 08:31:00 2021-05-13 08:43:00 0 days 00:12:00     0  
..         ...                 ...                 ...             ...   ...  
179   0.008661 2021-06-29 09:03:00 2021-06-29 09:08:00 0 days 00:05:00     0  
180  -0.000872 2021-07-01 12:03:00 2021-07-01 12:14:00 0 days 00:11:00     0  
181   0.004409 2021-07-06 09:12:00 2021-07-06 09:19:00 0 days 00:07:00     0  
182   0.004141 2021-07-07 04:58:00 2021-07-07 05:03:00 0 days 00:05:00     0  
183  -0.000523 2021-07-07 09:43:00 2021-07-07 09:56:00 0 days 00:13:00     0  

[184 rows x 11 columns]

In [282]:
trades_eth

Size  EntryBar  ExitBar   EntryPrice  ExitPrice          PnL  ReturnPct  \
0    -240      1682     1695  4160.115288    4170.82 -2569.130880  -0.002573   
1    -242      1863     1872  4104.837408    4075.45  7111.752736   0.007159   
2    -252      2189     2193  3978.727872    3942.26  9189.903744   0.009166   
3    -257      2341     2352  3939.243672    3952.69 -3455.706296  -0.003413   
4    -270      2792     2798  3733.945824    3713.50  5520.372480   0.005476   
..    ...       ...      ...          ...        ...          ...        ...   
248   617     73801    73813  2113.875212    2109.22 -2872.265804  -0.002202   
249  -573     78790    78808  2269.391880    2283.27 -7952.162760  -0.006115   
250  -585     79499    79511  2211.125196    2218.65 -4402.010340  -0.003403   
251   554     80403    80411  2324.929600    2335.00  5579.001600   0.004331   
252   559     81399    81412  2316.436204    2315.18  -702.218036  -0.000542   

              EntryTime            ExitTime        Duration  type  
0   2021-05-12 14:01:00 2021-05-12 14:14:00 0 days 00:13:00     1  
1   2021-05-12 17:02:00 2021-05-12 17:11:00 0 days 00:09:00     1  
2   2021-05-12 22:28:00 2021-05-12 22:32:00 0 days 00:04:00     1  
3   2021-05-13 01:00:00 2021-05-13 01:11:00 0 days 00:11:00     1  
4   2021-05-13 08:31:00 2021-05-13 08:37:00 0 days 00:06:00     1  
..                  ...                 ...             ...   ...  
248 2021-07-01 16:00:00 2021-07-01 16:12:00 0 days 00:12:00     1  
249 2021-07-05 03:09:00 2021-07-05 03:27:00 0 days 00:18:00     1  
250 2021-07-05 14:58:00 2021-07-05 15:10:00 0 days 00:12:00     1  
251 2021-07-06 06:02:00 2021-07-06 06:10:00 0 days 00:08:00     1  
252 2021-07-06 22:38:00 2021-07-06 22:51:00 0 days 00:13:00     1  

[253 rows x 11 columns]

In [288]:
total_trades = pd.concat([trades_btc, trades_eth])
len(total_trades)

437

In [290]:
total_trades_sorted = total_trades.sort_values('EntryTime')

In [294]:
total_trades_sorted['next_trade_time'] = total_trades_sorted['EntryTime'].shift(-1)

In [301]:
total_trades_sorted

Size  EntryBar  ExitBar    EntryPrice  ExitPrice          PnL  ReturnPct  \
0    -240      1682     1695   4160.115288    4170.82 -2569.130880  -0.002573   
1    -242      1863     1872   4104.837408    4075.45  7111.752736   0.007159   
0     -19      3069     3075  50433.588492   49944.47  9293.251348   0.009698   
2    -252      2189     2193   3978.727872    3942.26  9189.903744   0.009166   
1     -19      3158     3175  50569.744008   50504.89  1232.226152   0.001282   
..    ...       ...      ...           ...        ...          ...        ...   
251   554     80403    80411   2324.929600    2335.00  5579.001600   0.004331   
181   -40     81526    81533  34143.097296   33992.57  6021.091840   0.004409   
252   559     81399    81412   2316.436204    2315.18  -702.218036  -0.000542   
182    39     82712    82717  34648.593896   34792.07  5595.568056   0.004141   
183    39     82997    83010  34819.682304   34801.48  -709.889856  -0.000523   

              EntryTime            ExitTime        Duration  type  \
0   2021-05-12 14:01:00 2021-05-12 14:14:00 0 days 00:13:00     1   
1   2021-05-12 17:02:00 2021-05-12 17:11:00 0 days 00:09:00     1   
0   2021-05-12 21:35:00 2021-05-12 21:41:00 0 days 00:06:00     0   
2   2021-05-12 22:28:00 2021-05-12 22:32:00 0 days 00:04:00     1   
1   2021-05-12 23:04:00 2021-05-12 23:21:00 0 days 00:17:00     0   
..                  ...                 ...             ...   ...   
251 2021-07-06 06:02:00 2021-07-06 06:10:00 0 days 00:08:00     1   
181 2021-07-06 09:12:00 2021-07-06 09:19:00 0 days 00:07:00     0   
252 2021-07-06 22:38:00 2021-07-06 22:51:00 0 days 00:13:00     1   
182 2021-07-07 04:58:00 2021-07-07 05:03:00 0 days 00:05:00     0   
183 2021-07-07 09:43:00 2021-07-07 09:56:00 0 days 00:13:00     0   

        next_trade_time  OverlapsTime  
0   2021-05-12 17:02:00             0  
1   2021-05-12 21:35:00             0  
0   2021-05-12 22:28:00             0  
2   2021-05-12 23:04:00             0  
1   2021-05-13 01:00:00             0  
..                  ...           ...  
251 2021-07-06 09:12:00             0  
181 2021-07-06 22:38:00             0  
252 2021-07-07 04:58:00             0  
182 2021-07-07 09:43:00             0  
183                 NaT             0  

[437 rows x 13 columns]

In [304]:
sum(total_trades_sorted['OverlapsTime'])

95

In [296]:
total_trades_sorted['OverlapsTime'] = 0

In [297]:
total_trades_sorted.loc[total_trades_sorted['next_trade_time'] < total_trades_sorted['ExitTime'], 'OverlapsTime'] = 1

In [309]:
print('Total de trades overlapeados:', sum(total_trades_sorted['OverlapsTime'])/len(total_trades_sorted), '%')

Total de trades overlapeados: 0.21739130434782608 %


In [312]:
total_trades_sorted['OverlapsStart'] = 0

In [313]:
total_trades_sorted.loc[total_trades_sorted['next_trade_time'] == total_trades_sorted['EntryTime'], 'OverlapsStart'] = 1

In [314]:
print('Total de trades que comienzan al mismo momento:', sum(total_trades_sorted['OverlapsStart'])/len(total_trades_sorted), '%')

Total de trades que comienzan al mismo momento: 0.12356979405034325 %


## 6. Evaluo ultimo dia

In [21]:
from binance.client import Client
from datetime import datetime
from backtesting import Backtest, Strategy
from backtesting.lib import plot_heatmaps

import multiprocessing
import pandas as pd

# TODO: mover a variables de entorno
api_key = ''
secret_key = ''

client = Client(api_key, secret_key)


# bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '14 jun, 2021', '17 jun, 2021')
bars = client.get_historical_klines('BTCUSDT', Client.KLINE_INTERVAL_1MINUTE, '1 days ago')


def cast_string_to_float(data):
    if type(data) == str:
        casted_data = float(data)
    else:
        casted_data = datetime.fromtimestamp(data/1000.0)
    return casted_data

# delete unwanted data - just keep date, open, high, low, close
formated_bars = []
for line in bars:
    del line[6:]
    # cast string numbers to integer
    formated_bars.append(list(map(cast_string_to_float, line)))

#  store data in a dataframe
btc_df = pd.DataFrame(formated_bars, columns=['Date', 'Open', 'High', 'Low', 'Close', 'Volume'])
btc_df.set_index('Date', inplace=True)
# Converting the index as date
btc_df.index = pd.to_datetime(btc_df.index)

from talib import AROON, SMA, NATR, AROONOSC
import pandas as pd

class AroonPullback(Strategy):

    AROON_LENGTH = 30
    VOLUME_LENGTH = 10
    VOLUME_THRESHOLD = 15
    SMA_LENGTH = 15
    NATR_THRESHOLD_MR = 36
    VOLATILITY_LENGTH = 60
    VOLATILITY_THRESHOLD = 0
    TF_MODE = False

    def VOLUME_AVG(self, volume):
       return pd.Series(volume).rolling(self.VOLUME_LENGTH).mean()

    def EMA_AVG(self, data):
        return pd.Series(data).ewm(span=self.BULL_BEAR_MARKET_EMA_THRESHOLD).mean()

    def STD_DEV(self, data):
        pct_changes = pd.Series(data).pct_change() * 100
        return pct_changes.rolling(self.VOLATILITY_LENGTH).std() 

    def init(self):
        self.aroondown, self.aroonup = self.I(AROON, self.data.High, self.data.Low, timeperiod = self.AROON_LENGTH)
        self.volume_avg = self.I(self.VOLUME_AVG, self.data.Volume)
        self.mean_price = self.I(SMA, self.data.Close, timeperiod=self.SMA_LENGTH)
        self.natr = self.I(NATR, self.data.High, self.data.Low, self.data.Close, timeperiod = 2)
        self.std_dev = self.I(self.STD_DEV, self.data.Close)

    def next(self):
        if (not self.position and self.natr > (self.NATR_THRESHOLD_MR/100)):
            if (self.aroonup == 100 and self.data.Volume > (self.VOLUME_THRESHOLD / 10 * self.volume_avg)):
                if (self.is_market_volatility_high()):
                    self.sell()
            elif(self.aroondown == 100 and self.data.Volume > (self.VOLUME_THRESHOLD / 10 * self.volume_avg)):
                if (self.is_market_volatility_high()):
                    self.buy()
        else:
            if (self.position.is_long and self.data.Close >= self.mean_price):
                self.position.close()
            elif (self.position.is_short and self.data.Close <= self.mean_price):
                self.position.close()

    def is_market_volatility_high(self):
        return self.std_dev > (self.VOLATILITY_THRESHOLD / 1000)

bt = Backtest(btc_df, AroonPullback, cash=1000000, commission=.0004, exclusive_orders=True, margin=0.2)
stats = bt.run()

bt.plot()

/Users/nelsonrios/opt/anaconda3/lib/python3.8/site-packages/backtesting/backtesting.py:1584: RuntimeWarning: divide by zero encountered in double_scalars
  s.loc['Sortino Ratio'] = np.clip(annualized_return / (np.sqrt(np.mean(day_returns.clip(-np.inf, 0)**2)) * np.sqrt(annual_trading_days)), 0, np.inf)  # noqa: E501


In [22]:
stats._trades

Size  EntryBar  ExitBar    EntryPrice  ExitPrice           PnL  ReturnPct  \
0   159       830      841  31343.102228   31361.97   2999.975748   0.000602   
1   159      1287     1299  31513.720448   31587.81  11780.238768   0.002351   

            EntryTime            ExitTime        Duration  
0 2021-07-18 11:41:00 2021-07-18 11:52:00 0 days 00:11:00  
1 2021-07-18 19:18:00 2021-07-18 19:30:00 0 days 00:12:00